# Data Management and Database Design INFO 6210

### How you converted SQL database (SQL Project database) into its NoSQL equivalent :



For converting the SQL database into non relational database, here we have created a script which does all the work of converting the data into required format for MongoDB

#### Importing all the required packages for running the script to convert SQL to nonRelational Database

In [1]:
from pymongo import MongoClient
import sqlite3
import json
import pandas as pd

Here, I've done this project on MacOS High Sierra. 

To start a Mongo server we run the following command in terminal  

>`mongod --dbpath [path to database file]`

To access MongoDB on terminal we use the following command

>`mongo`

#### Connecting to MongoDB and switching to required Collection. 

In [2]:
client = MongoClient('localhost', 27017)  #Connection to MongoDB
db=client.project   #Switching to Collection with name 'assignment3'

#### Connecting to SQLITE3 and switching to required Database 

In [3]:
connection = sqlite3.connect("projectTwit.db")
cursor = connection.cursor()
cursor2 = connection.cursor()
cursor3 = connection.cursor()

There are following tables in SQL database

`User`  
```
(user_id varchar(25) not null primary key , user_name varchar(50), followers int, following int, tweet_count int)
```
Here **user_id** is the Primary Key

`Tweet` 
```
(tweet_id varchar(25) not null primary key, user_id varchar(25),tweet_content varchar(300), urls varchar(100))
```
Here **tweet_id** is the Primary Key

`Tweet_details`  
```
(tweet_id varchar(25) not null primary key, date varchar(10),time varchar(8), favourate int, retweets int )
```
Here **tweet_id** is the Primary Key

`Tags` 
```
(tag_id integer not null primary key autoincrement, tag_details varchar(50) )
```
Here **tag_id** is the Primary Key

`User_tags`
```
(tag_no integer not null primary key autoincrement, user_id varchar(25), tag_id varchar(25))
```
Here **tag_no** is the Primary Key

`Tweet_tags` 
```
(tag_no integer not null primary key autoincrement, tweet_id varchar(25), tag_id varchar(25))
```
Here **tag_no** is the Primary Key


The formatting of data in SQL is done to satisfy the conditions of normalization. 

Thus we have different tables of `USER` , `Tweet` and  `Tweet_details`.

We also have tables for `Tags` which Tag_Id and Tag_details, we are then creating relational tables `user_tags` and `tweet_tags` to store data for all users.

We also have tables of *mispellings* and *synonyms*. But we use these while populating tags for users, to see if there is any mistake in spelling or if any Synonym is being used. 

In MongoDB we will have the following collections 
```
Collection user:
{
 	"user_id":"Data String",
 	"user_name":"Data String",
 	"followers": Data Int,
 	"following": Data Int,
 	"tweet_count": Data Int,
 	"hashtags":[ ]
}
```
```
Collection tweet:
{
 	"tweet_id": "Data String",
 	"user_id": "Data String",
 	"tweet_contents": "Data String",
 	"urls": "Data String",
 	"date": "Data String",
 	"time": "Data String",
 	"favourites": Data Int,
 	"retweets": Data Int,
 	"hashtags":[ ]
}
```
In the above collections we have *Hashtags* as a **List** in *Json* 


We need not insert tags_id into the database.

Instead we will directly insert all the tags for a tweet or a user directly in *List (hashtags)* in the document.

Document User will have all the data of that user and tags directly in the document 

Similarly, Document Tweet will have data from tweet table and tweet_details

Both the Documents will have hashtags as a list instead if three different tables as in SQL

### Transfering Data

Here we have written a functions which extracts data from SQL in our required format and converts it into **JSON** file compatible for MongoDB and this **JSON** is directly inserted into the required document. 


#### Populate User Document with data from SQL

In [4]:
def getAndPopulateUsers():

    mainQuery="Select * from user"

    for row in cursor.execute(mainQuery):

        output= "SELECT tag_id from user_tags where user_id='"+ row[0]+"' "
        list = []
        for row2 in cursor2.execute(output):
            getTag="select tag_details from tags where tag_id='"+row2[0]+"'"
            tagName=cursor3.execute(getTag)
            list.append(tagName.fetchone()[0])
        res= ('{ "user_id": "%s" , "user_name": "%s", "followers": %d, "following": %d, "tweet_count": %d, "hashtags": %s  }' %(row[0],row[1],row[2],row[3],row[4], str(list).replace("'","\"").replace("u","").replace("\\","")))
        print (res)
        db.user.insert_one(json.loads(res))


Here, the **mainquery** variable is used to extract all the data from the user table.

For every user, we extract tags related to that user and add them to a list.

We will insert this list into hashtags column directly. This can be done, because, MongoDB uses unstructured document to store data. Also known as `BSON`

#### Populate Tweet Document with data from SQL

In [5]:
def getandPopulateTweets():

    mainQuery=" Select * from tweet inner join tweet_details where tweet.tweet_id=tweet_details.tweet_id"

    for row in cursor.execute(mainQuery):
        output = "SELECT tag_id from tweet_tags where tweet_id='" + row[0] + "' "
        list = []
        for row2 in cursor2.execute(output):
            getTag = "select tag_details from tags where tag_id='" + row2[0] + "'"
            tagName = cursor3.execute(getTag)
            list.append(tagName.fetchone()[0])
        res= ('{ "tweet_id": "%s", "user_id": "%s", "tweet_contents": "%s", "urls": "%s", "date": "%s", "time": "%s", "favourites": %d, "retweets": %d, "hashtags": %s }'  %(row[0], row[1], row[2].replace("\n"," ").replace("\"",""), row[3], row[5], row[6], row[7], row[8], str(list).replace("'","\"").replace("u\"","\"").replace("\\","")   ))
        print (res)
        db.tweet.insert_one(json.loads(res))

Similar to User Document, we will populate the tweet document by extracting the data from SQL with queries and converting them to **JSON** format

In the above two functions, it can be observed that, we are replacing few characters from the data and substituting with some another character, or we are adding an escape character. This is done to make the data compitable with JSON, i.e some inverted commas or double inverted commas can cause abnormal termination of string.

#### Data from SQL Tables 

In [6]:
output= "SELECT * from user Limit 5"
cursor.execute(output)
pd.DataFrame(cursor.fetchall(), columns=['user_id','user_name','followers','following','tweet_count'])

user_id              user_name  followers  following  tweet_count
0           @ExpoDX          DXWorldEXPO ®        521          0         3709
1     @TechNewsRprt        TechNews Report       4045       3059         5882
2      @ScopeOnline                  SCOPE       2635       2127        11505
3        @nschaetti  NS.ai (Nils Schaetti)       8332       7928        91810
4  @gabrielanthonyp      GabrielAnthony P.       2391       3939        79443

In [7]:
output= "SELECT * from tweet Limit 3"
cursor.execute(output)
pd.DataFrame(cursor.fetchall(), columns=['tweet_id','user_id','tweet_content','urls'])

tweet_id        user_id  \
0  968036614202150912        @ExpoDX   
1  968036597634564096        @ExpoDX   
2  968036559638482944  @TechNewsRprt   

                                       tweet_content  \
0  RT @ExpoDX: AI, Monitoring and Digital Transfo...   
1  AI, Monitoring and Digital Transformation with...   
2  RT @TamaraMcCleary: Tech Trends That Will Impa...   

                                                urls  
0                                             NO_URL  
1  https://twitter.com/i/web/status/9680365976345...  
2                                             NO_URL

In [8]:
output= "SELECT * from tweet_details Limit 3"
cursor.execute(output)
pd.DataFrame(cursor.fetchall(), columns=['tweet_id','date','time','favourate','retweet'])

tweet_id        date      time  favourate  retweet
0  968036614202150912  2018-02-26  08:14:48          0        2
1  968036597634564096  2018-02-26  08:14:44          1        2
2  968036559638482944  2018-02-26  08:14:35          0       77

In [9]:
output= "SELECT * from tags Limit 3"
cursor.execute(output)
pd.DataFrame(cursor.fetchall(), columns=['tag_id','tag_details'])

tag_id  tag_details
0     654  cloudnative
1     655          apm
2     656        linux

In [10]:
output= "SELECT * from user_tags Limit 3"
cursor.execute(output)
pd.DataFrame(cursor.fetchall(), columns=['tag_no','user_id','tag_id'])

tag_no  user_id tag_id
0    3946  @ExpoDX    654
1    3947  @ExpoDX    655
2    3948  @ExpoDX    656

In [11]:
output= "SELECT * from tweet_tags Limit 3"
cursor.execute(output)
pd.DataFrame(cursor.fetchall(), columns=['tag_no','tweet_id','tag_id'])

tag_no            tweet_id tag_id
0    4014  968036614202150912    654
1    4015  968036614202150912    655
2    4016  968036614202150912    656

Let's Run the above two code statements [ getAndPopulateUsers( ) , getAndPopulateTweets( ) ] to migrate data from SQL to MongoDB 

In [12]:
getAndPopulateUsers()

{ "user_id": "@ExpoDX" , "user_name": "DXWorldEXPO ®", "followers": 521, "following": 0, "tweet_count": 3709, "hashtags": ["clodnative", "apm", "linx", "serverless", "devops", "bigdata", "clod", "iot", "iiot"]  }
{ "user_id": "@TechNewsRprt" , "user_name": "TechNews Report", "followers": 4045, "following": 3059, "tweet_count": 5882, "hashtags": ["infographic", "digitaltransformation", "ai", "marketing", "mwc18", "ericssondigital", "bigdata"]  }
{ "user_id": "@ScopeOnline" , "user_name": "SCOPE", "followers": 2635, "following": 2127, "tweet_count": 11505, "hashtags": ["artificialintelligence", "deeplearning", "machinelearning", "atomation"]  }
{ "user_id": "@nschaetti" , "user_name": "NS.ai (Nils Schaetti)", "followers": 8332, "following": 7928, "tweet_count": 91810, "hashtags": ["ai", "machinelearning", "ia", "bigdata", "datascience", "robots", "robotic", "intelligenceartificielle", "deeplearning", "artificialintelligence"]  }
{ "user_id": "@gabrielanthonyp" , "user_name": "GabrielAnth

{ "user_id": "@matterofminds" , "user_name": "Ideas For Growth", "followers": 2758, "following": 360, "tweet_count": 166549, "hashtags": ["twitteratomation", "inbond", "lowcost"]  }
{ "user_id": "@BryanJPalma" , "user_name": "Bryan Palma", "followers": 7344, "following": 85, "tweet_count": 693, "hashtags": []  }
{ "user_id": "@Rajivjoshi1985" , "user_name": "Rajiv Joshi", "followers": 152, "following": 194, "tweet_count": 4568, "hashtags": []  }
{ "user_id": "@KUKA_RoboticsEN" , "user_name": "KUKA Robotics", "followers": 16870, "following": 381, "tweet_count": 6113, "hashtags": ["coffee", "indstrie40", "i40", "atomation", "robots"]  }
{ "user_id": "@JacobusSystems" , "user_name": "Jacobus Systems Ltd.", "followers": 532, "following": 205, "tweet_count": 94444, "hashtags": []  }
{ "user_id": "@CRMHourlyNews" , "user_name": "CRM Hourly News", "followers": 2935, "following": 1589, "tweet_count": 38047, "hashtags": ["crm"]  }
{ "user_id": "@IteratorsLLC" , "user_name": "Iterators", "follow

{ "user_id": "@birdsongnz" , "user_name": "Cacophony Project", "followers": 588, "following": 1688, "tweet_count": 212, "hashtags": []  }
{ "user_id": "@deeplearnbot" , "user_name": "deeplearnbot", "followers": 62, "following": 30, "tweet_count": 2252, "hashtags": ["bigdata", "datascience", "digitalmarketing", "ai", "machinelearning", "deeplearning"]  }
{ "user_id": "@data_d1va" , "user_name": "Lou Potts", "followers": 231, "following": 250, "tweet_count": 3782, "hashtags": ["analytics", "datascience", "ibmml", "iot", "machinelearning"]  }
{ "user_id": "@innarticle" , "user_name": "Innocent Udeogu", "followers": 340, "following": 290, "tweet_count": 748, "hashtags": []  }
{ "user_id": "@BourseetTrading" , "user_name": "Anthony Schmitt Financial Services", "followers": 14803, "following": 615, "tweet_count": 65931, "hashtags": ["ai", "blockchain", "robots", "iot", "machinelearning", "bigdataanalytics", "infrastrctre", "fintech", "atomation", "pwc"]  }
{ "user_id": "@Rad_Reza" , "user_na

{ "user_id": "@ccwells" , "user_name": "Charlie Wells", "followers": 653, "following": 1247, "tweet_count": 3774, "hashtags": []  }
{ "user_id": "@jessie_bur" , "user_name": "Jessie Bur", "followers": 256, "following": 236, "tweet_count": 527, "hashtags": ["atomation"]  }
{ "user_id": "@SeymenYunus" , "user_name": "#beattokenICO Yunus Seymen", "followers": 1527, "following": 1857, "tweet_count": 2357, "hashtags": []  }
{ "user_id": "@durgeshskumar" , "user_name": "Durgesh Tantiya", "followers": 696, "following": 111, "tweet_count": 53817, "hashtags": ["atomation", "edge", "cybersecrity"]  }
{ "user_id": "@simonbullhorn" , "user_name": "Simon Greening", "followers": 1288, "following": 834, "tweet_count": 3885, "hashtags": []  }
{ "user_id": "@IT_securitynews" , "user_name": "IT Security News", "followers": 7108, "following": 491, "tweet_count": 396323, "hashtags": ["infosec"]  }
{ "user_id": "@sorinmustaca" , "user_name": "Sorin Mustaca", "followers": 1496, "following": 457, "tweet_coun

{ "user_id": "@Inventumcloud" , "user_name": "Inventum Cloud", "followers": 417, "following": 1014, "tweet_count": 1565, "hashtags": []  }
{ "user_id": "@Xborder3" , "user_name": "Xborder.ai", "followers": 56, "following": 142, "tweet_count": 56, "hashtags": []  }
{ "user_id": "@InventumAaaS" , "user_name": "Inventum Analytics", "followers": 739, "following": 1064, "tweet_count": 1427, "hashtags": []  }
{ "user_id": "@bedfordcj" , "user_name": "Caroline Bedford", "followers": 3134, "following": 607, "tweet_count": 5462, "hashtags": []  }
{ "user_id": "@DX_Innova" , "user_name": "DX iNNOVa", "followers": 139, "following": 211, "tweet_count": 308, "hashtags": []  }
{ "user_id": "@BigdataSMB" , "user_name": "Big Data for SMB", "followers": 658, "following": 579, "tweet_count": 1083, "hashtags": []  }
{ "user_id": "@nanseninsights" , "user_name": "Smartdata", "followers": 19, "following": 68, "tweet_count": 164, "hashtags": []  }
{ "user_id": "@ZakyHiromasa" , "user_name": "Penulis Biograf

...

{ "user_id": "@rtehrani" , "user_name": "Rich Tehrani", "followers": 14119, "following": 9111, "tweet_count": 39229, "hashtags": ["ai", "blockchain", "cheating", "amazon"]  }
{ "user_id": "@ume_kyd" , "user_name": "ume", "followers": 1027, "following": 1016, "tweet_count": 1417, "hashtags": ["fnddistribtion", "network", "world", "startp", "lxemborg", "innovation", "dream", "life", "fnd", "passion", "live", "fire"]  }
{ "user_id": "@stochasticdoggo" , "user_name": "Katrina Evtimova", "followers": 56, "following": 98, "tweet_count": 44, "hashtags": ["machinelearning"]  }
{ "user_id": "@seancostigan" , "user_name": "sean costigan", "followers": 847, "following": 380, "tweet_count": 12725, "hashtags": []  }
{ "user_id": "@VeroniquePretre" , "user_name": "VeroniquePretre", "followers": 326, "following": 357, "tweet_count": 4264, "hashtags": ["artificialintelligence"]  }
{ "user_id": "@olegpocheff" , "user_name": "Oleh Podvysotskyi", "followers": 18, "following": 330, "tweet_count": 44, "has

{ "user_id": "@tunguz" , "user_name": "Bojan Tunguz", "followers": 4228, "following": 3315, "tweet_count": 41211, "hashtags": ["ai", "artificialintelligence", "deeplearning", "datascience", "machinelearning", "bigdata"]  }
{ "user_id": "@BasilBrylcreem" , "user_name": "John Frazier", "followers": 227, "following": 131, "tweet_count": 10533, "hashtags": ["robot", "deeplearning", "data", "analytics"]  }
{ "user_id": "@Alberic2Menou" , "user_name": "Albéric de Menou", "followers": 116, "following": 284, "tweet_count": 922, "hashtags": ["ai"]  }
{ "user_id": "@Auual" , "user_name": "AK", "followers": 330, "following": 450, "tweet_count": 12467, "hashtags": ["datascience", "abdsc"]  }
{ "user_id": "@Gavboss_" , "user_name": "🇯🇲Balance☯⚖♎️Libra", "followers": 1683, "following": 1059, "tweet_count": 116490, "hashtags": []  }
{ "user_id": "@infi_intel_info" , "user_name": "InfiniteIntelligenceGroup", "followers": 1, "following": 17, "tweet_count": 28, "hashtags": ["artificialintelligence", "st

{ "user_id": "@brett_hudecek" , "user_name": "Brett hudecek", "followers": 316, "following": 23, "tweet_count": 182, "hashtags": ["waltonchain"]  }
{ "user_id": "@BonnieFRobinson" , "user_name": "Bonnie Robinson", "followers": 3562, "following": 3188, "tweet_count": 6426, "hashtags": ["iot", "healthcare", "fintech", "cybersecrity", "infosec"]  }
{ "user_id": "@markosankovic" , "user_name": "Marko Sanković", "followers": 85, "following": 187, "tweet_count": 190, "hashtags": []  }
{ "user_id": "@dtcjrenergy" , "user_name": "David Cooke Jr.", "followers": 131, "following": 86, "tweet_count": 12537, "hashtags": []  }
{ "user_id": "@gabriel_anzaldi" , "user_name": "Gabriel Anzaldi", "followers": 435, "following": 380, "tweet_count": 5228, "hashtags": ["grape", "robxf3tica"]  }
{ "user_id": "@mchallamlaw" , "user_name": "Chris", "followers": 4506, "following": 4994, "tweet_count": 160111, "hashtags": []  }
{ "user_id": "@von__bomb" , "user_name": "von bon jovi", "followers": 451, "following"

{ "user_id": "@gasiber" , "user_name": "Gasiber", "followers": 3102, "following": 5002, "tweet_count": 19455, "hashtags": ["ai", "machinelearning", "deeplearning", "bigdata"]  }
{ "user_id": "@PythonSV" , "user_name": "Python SV e.V.", "followers": 788, "following": 173, "tweet_count": 3225, "hashtags": ["pydata"]  }
{ "user_id": "@ekholabs" , "user_name": "ekholabs", "followers": 64, "following": 64, "tweet_count": 850, "hashtags": ["sinerel", "keras", "machinelearning"]  }
{ "user_id": "@wilderrodrigues" , "user_name": "The Ekho", "followers": 389, "following": 358, "tweet_count": 4765, "hashtags": ["sinerel", "keras", "machinelearning"]  }
{ "user_id": "@ElsenInc" , "user_name": "Elsen Inc.", "followers": 697, "following": 1301, "tweet_count": 6646, "hashtags": ["machinelearning", "ai", "insrtech"]  }
{ "user_id": "@Parthesh_Raval" , "user_name": "partheshraval", "followers": 2249, "following": 1902, "tweet_count": 11826, "hashtags": ["ai", "machinelearning", "deeplearning", "bigdat

{ "user_id": "@maxreig" , "user_name": "Max Reig", "followers": 300, "following": 343, "tweet_count": 3053, "hashtags": []  }
{ "user_id": "@asiya_asha" , "user_name": "Asiya Asha あ", "followers": 703, "following": 1209, "tweet_count": 211, "hashtags": []  }
{ "user_id": "@MixMegaMarket" , "user_name": "MixMegaMarket", "followers": 30491, "following": 35050, "tweet_count": 6397, "hashtags": []  }
{ "user_id": "@jprendek" , "user_name": "John Rendek", "followers": 173, "following": 370, "tweet_count": 342, "hashtags": []  }
{ "user_id": "@johnnatan96" , "user_name": "Johnnatan Jaramillo", "followers": 139, "following": 946, "tweet_count": 329, "hashtags": ["deeplearning"]  }
{ "user_id": "@apfel94" , "user_name": "Michael R.", "followers": 355, "following": 2000, "tweet_count": 2428, "hashtags": ["gtc18", "deeplearning"]  }
{ "user_id": "@Data_MSci" , "user_name": "Data MSci", "followers": 4910, "following": 2695, "tweet_count": 7520, "hashtags": ["datascience", "machinelearning", "deep

In the above output, we can see all the converted **JSON** files printed as we enter them to MongoDB document. 

Similarly we do it for tweets Below. 

In [14]:
getandPopulateTweets()

{ "tweet_id": "968036614202150912", "user_id": "@ExpoDX", "tweet_contents": "RT @ExpoDX: AI, Monitoring and Digital Transformation with @SaboTaylorDiab  @Loom_Systems #CloudNative #APM #Linux #Serverless #DevOps #Dat…", "urls": "NO_URL", "date": "2018-02-26", "time": "08:14:48", "favourites": 0, "retweets": 2, "hashtags": ["cloudnative", "apm", "linux", "serverless", "devops"] }
{ "tweet_id": "968036597634564096", "user_id": "@ExpoDX", "tweet_contents": "AI, Monitoring and Digital Transformation with @SaboTaylorDiab  @Loom_Systems #CloudNative #APM #Linux #Serverless… https://t.co/5CaXydsQEp", "urls": "https://twitter.com/i/web/status/968036597634564096", "date": "2018-02-26", "time": "08:14:44", "favourites": 1, "retweets": 2, "hashtags": ["cloudnative", "apm", "linux", "serverless"] }
{ "tweet_id": "968036559638482944", "user_id": "@TechNewsRprt", "tweet_contents": "RT @TamaraMcCleary: Tech Trends That Will Impact Your Business In The Next 4 Years // #Infographic #DigitalTransformati

{ "tweet_id": "968008311344943104", "user_id": "@ShawkyBenkhodja", "tweet_contents": "RT @ipfconline1: Population Based Training of #NeuralNetworks  https://t.co/sJfgohMRU8    [by @maxjaderberg v/ @deepmindai] #AI #MachineLea…", "urls": "https://buff.ly/2l7ur8a", "date": "2018-02-26", "time": "06:22:20", "favourites": 0, "retweets": 22, "hashtags": ["neuralnetworks", "ai"] }
{ "tweet_id": "968008133309272064", "user_id": "@StrategyFintech", "tweet_contents": "RT @pierrepinna: #DeepLearning Achievements Over the Past Year  https://t.co/6gT4t4r6H7 @statsbotco   #AI #MachineLearning #NeuralNetworks…", "urls": "https://buff.ly/2BQ1k32", "date": "2018-02-26", "time": "06:21:38", "favourites": 0, "retweets": 19, "hashtags": ["deeplearning", "ai", "machinelearning", "neuralnetworks"] }
{ "tweet_id": "968008028292288512", "user_id": "@JohnSnowai", "tweet_contents": "RT @pierrepinna: #DeepLearning Achievements Over the Past Year  https://t.co/6gT4t4r6H7 @statsbotco   #AI #MachineLearning #Neura

{ "tweet_id": "968035031414276096", "user_id": "@iotfacts", "tweet_contents": "Chinese scientists develop AI system to diagnose human diseases | https://t.co/wTBZnogm1t #DeepLearning", "urls": "http://on.china.cn/2CjWgoB", "date": "2018-02-26", "time": "08:08:31", "favourites": 0, "retweets": 0, "hashtags": ["deeplearning"] }
{ "tweet_id": "968034958853005318", "user_id": "@SEOSMOIndore", "tweet_contents": "RT @Fifium_Social: What is the importance for #SEO services for a #business ? Find out the most relevant answer to this question, with FIFI…", "urls": "NO_URL", "date": "2018-02-26", "time": "08:08:14", "favourites": 0, "retweets": 1, "hashtags": ["seo", "business"] }
{ "tweet_id": "968034942104961024", "user_id": "@RobinTh0mson", "tweet_contents": "RT @IainLJBrown: #Canon Intros Speedlite 470EX-AI Flash with New Auto Intelligent Bounce Technology https://t.co/EgMEU0BGuM https://t.co/aO…", "urls": "https://goo.gl/eBX2p5", "date": "2018-02-26", "time": "08:08:10", "favourites": 0, "r

{ "tweet_id": "968036694703398912", "user_id": "@gioachinoasti77", "tweet_contents": "RT @S_Galimberti: If an AI creates a work of art, who owns the copyright? https://t.co/4CkYUdvXT4 #ArtificialIntelligence https://t.co/WdEc…", "urls": "http://wef.ch/2ohQNoO", "date": "2018-02-26", "time": "08:15:07", "favourites": 0, "retweets": 3, "hashtags": ["artificialintelligence"] }
{ "tweet_id": "968037199076823041", "user_id": "@GijsHuisman", "tweet_contents": "RT @we_are_inspark: Op 13 maart hosten wij een Microsoft Data Science meetup over Build your own Bot. Dataexperts @jeroenterheerdt en @DrGi…", "urls": "NO_URL", "date": "2018-02-26", "time": "08:17:08", "favourites": 0, "retweets": 8, "hashtags": [] }
{ "tweet_id": "968036871401033728", "user_id": "@pridgeefx", "tweet_contents": "RT @SASsoftwareUK: The big challenges for graduates moving into the world of #datascience. And how SAS is helping resolve them. https://t.c…", "urls": "NO_URL", "date": "2018-02-26", "time": "08:15:50", "favou

{ "tweet_id": "968225320687030272", "user_id": "@ActiveBatch", "tweet_contents": "Transform your #Informatica #automation: https://t.co/8oqXf1qUos The case for workload automation #devops #iot #IT #bigdata", "urls": "http://bit.ly/2ETb13l", "date": "2018-02-26", "time": "20:44:39", "favourites": 0, "retweets": 0, "hashtags": ["informatica", "automation", "devops", "iot", "it", "bigdata"] }
{ "tweet_id": "968225314475331584", "user_id": "@Science_Mktg", "tweet_contents": "#RT @MktgSciences: Major banks and traders test #BlockChain platform for commodity trade https://t.co/vHvdHurZ2l… https://t.co/w149js48kO", "urls": "http://www.gtreview.com.convey.pro/l/jVMpo71", "date": "2018-02-26", "time": "20:44:38", "favourites": 0, "retweets": 0, "hashtags": ["rt", "blockchain"] }
{ "tweet_id": "968225309156835331", "user_id": "@Science_Mktg", "tweet_contents": "#RT @MktgSciences: A Data Lake For Banking: A SnapLogic Story https://t.co/AdLB9BEIuX #bigdata #datascience #hadoop… https://t.co/YObDfH

...

{ "tweet_id": "975833100897914880", "user_id": "@audio", "tweet_contents": "Automation doesn t just save cash, it can also greatly enhance the customer experience. #entrepreneur… https://t.co/27TGuCidIA", "urls": "https://twitter.com/i/web/status/975833100897914880", "date": "2018-03-19", "time": "20:35:16", "favourites": 0, "retweets": 0, "hashtags": ["entrepreneur"] }
{ "tweet_id": "975833076399005697", "user_id": "@eagle_drones_us", "tweet_contents": "Severe #solarstorms could stop self-driving cars dead in their tracks  https://t.co/BJbt5GhQdX  #RoadSafety #roads… https://t.co/G39HHgC4nr", "urls": "https://buff.ly/2tWlA0t", "date": "2018-03-19", "time": "20:35:10", "favourites": 0, "retweets": 0, "hashtags": ["solarstorms", "roadsafety", "roads"] }
{ "tweet_id": "975833067033169920", "user_id": "@Epitomise_Ltd", "tweet_contents": "12 steps to cost-effective #agilemarketing campaigns. Use simple automation, minimum viable &amp; repurposed content, s… https://t.co/06amAQNF2C", "urls"

{ "tweet_id": "975831859643985921", "user_id": "@AGU_SciComm", "tweet_contents": "AI writing bots are about to revolutionize science journalism: we must shape how this is done… https://t.co/NKelxsoihe", "urls": "https://twitter.com/i/web/status/975831859643985921", "date": "2018-03-19", "time": "20:30:20", "favourites": 0, "retweets": 0, "hashtags": [] }
{ "tweet_id": "975831849066024964", "user_id": "@IndeedAU", "tweet_contents": "Whilst advances in #AI have stoked fears of large-scale job losses, there is another side to the coin.… https://t.co/b1cIZVBo3g", "urls": "https://twitter.com/i/web/status/975831849066024964", "date": "2018-03-19", "time": "20:30:17", "favourites": 0, "retweets": 0, "hashtags": ["ai"] }
{ "tweet_id": "975831813938647042", "user_id": "@MarutiTech", "tweet_contents": "The Real Time Self-Service Solution For Online Customer Service: AI https://t.co/KFavi0MhPh via @inc42 #ArtificialIntelligence", "urls": "https://sb.gl/2GHCG4W", "date": "2018-03-19", "time": "20

{ "tweet_id": "979812278232109057", "user_id": "@HubadevKP", "tweet_contents": "RT @Ronald_vanLoon: How to Get Actionable #Data from @Google #Analytics in 10 Minutes by @neilpatel |  Read more at https://t.co/DpAc76JGCf…", "urls": "http://bit.ly/2nTeHIn", "date": "2018-03-30", "time": "20:07:05", "favourites": 0, "retweets": 6, "hashtags": ["data", "analytics"] }
{ "tweet_id": "979812270132940800", "user_id": "@Tsundu_Mak", "tweet_contents": "RT @Edvancer: Until recently, most applications in AI and machine learning fell into one of two categories: supervised &amp; unsupervised learn…", "urls": "NO_URL", "date": "2018-03-30", "time": "20:07:03", "favourites": 0, "retweets": 1, "hashtags": [] }
{ "tweet_id": "979812248133783552", "user_id": "@Calcaware", "tweet_contents": "RT @bobehayes: Most Used #DataScience Tools and Technologies in 2017 and What to Expect for 2018  https://t.co/QqiuPWMdIA #machinelearning…", "urls": "http://bit.ly/2ClyER1", "date": "2018-03-30", "time": "20:06:58", 

{ "tweet_id": "979794254879801344", "user_id": "@harryshum", "tweet_contents": "RT @MSFTResearch: Microsoft Research Talks take a deeper dive into some of today s most groundbreaking #research like Neural Homology Theor…", "urls": "NO_URL", "date": "2018-03-30", "time": "18:55:28", "favourites": 0, "retweets": 12, "hashtags": ["research"] }
{ "tweet_id": "979794079868317696", "user_id": "@SaulButcher", "tweet_contents": "RT @KirkDBorne: 21 popular articles about #DeepLearning and #DataScience at @DataScienceCtrl https://t.co/OUXF09rm2I #abdsc #BigData #Machi…", "urls": "http://bit.ly/2AbiuEO", "date": "2018-03-30", "time": "18:54:46", "favourites": 0, "retweets": 49, "hashtags": ["deeplearning", "datascience", "abdsc", "bigdata"] }
{ "tweet_id": "979794055243714560", "user_id": "@alevergara78", "tweet_contents": "RT @girish4growth: Step by Step, AI Is Accelerating the Search for a Cancer Cure #AI #MachineLearning #Deeplearning #BigData #Datascience #…", "urls": "NO_URL", "date": "2018-

{ "tweet_id": "979810617900064768", "user_id": "@VulnerableWin", "tweet_contents": "RT @TessaMakesLove: Love &amp; Automation: The Creepy Touch of a Mechanical Mother https://t.co/cJuCIXJfyv #human   Love is something that is l…", "urls": "https://buff.ly/2pHG4EZ", "date": "2018-03-30", "time": "20:00:29", "favourites": 0, "retweets": 2, "hashtags": ["human"] }
{ "tweet_id": "979810599025639424", "user_id": "@RossBioFuel", "tweet_contents": "RT @KADGLOBAL: #IoT and #automation could usher in a new era of water conservation in #Africa https://t.co/ZOmqdwlXGd @thegbcghana #IIoT #s…", "urls": "https://bit.ly/2pJoQHo", "date": "2018-03-30", "time": "20:00:25", "favourites": 0, "retweets": 4, "hashtags": ["iot", "automation"] }
{ "tweet_id": "979810598299959296", "user_id": "@GreggRyeson", "tweet_contents": "If you’ve ever dreamed of living in the #SmartHome of the future, there’s good news: with these 5 #smart #devices,… https://t.co/BYqwRGiwYf", "urls": "https://twitter.com/i/web/status/9

##### Lets Query data from our newly migrated data to MongoDB

In [15]:
user=db.user
tweet=db.tweet

Here, we gave the cursor for db.user to a variable user and db.tweet to variable tweet.

In [16]:
output= user.find({})
for data in list(output):
    print data

{u'user_id': u'@ExpoDX', u'user_name': u'DXWorldEXPO \xae', u'hashtags': [u'clodnative', u'apm', u'linx', u'serverless', u'devops', u'bigdata', u'clod', u'iot', u'iiot'], u'followers': 521, u'following': 0, u'_id': ObjectId('5ada4426ec661529fc12d319'), u'tweet_count': 3709}
{u'user_id': u'@TechNewsRprt', u'user_name': u'TechNews Report', u'hashtags': [u'infographic', u'digitaltransformation', u'ai', u'marketing', u'mwc18', u'ericssondigital', u'bigdata'], u'followers': 4045, u'following': 3059, u'_id': ObjectId('5ada4426ec661529fc12d31a'), u'tweet_count': 5882}
{u'user_id': u'@ScopeOnline', u'user_name': u'SCOPE', u'hashtags': [u'artificialintelligence', u'deeplearning', u'machinelearning', u'atomation'], u'followers': 2635, u'following': 2127, u'_id': ObjectId('5ada4426ec661529fc12d31b'), u'tweet_count': 11505}
{u'user_id': u'@nschaetti', u'user_name': u'NS.ai (Nils Schaetti)', u'hashtags': [u'ai', u'machinelearning', u'ia', u'bigdata', u'datascience', u'robots', u'robotic', u'intelli

{u'user_id': u'@jgregorymartin', u'user_name': u'Greg Martin', u'hashtags': [], u'followers': 296, u'following': 596, u'_id': ObjectId('5ada4428ec661529fc12dacc'), u'tweet_count': 45725}
{u'user_id': u'@TheRealTWolf3', u'user_name': u'TWolf3', u'hashtags': [], u'followers': 446, u'following': 1786, u'_id': ObjectId('5ada4428ec661529fc12dacd'), u'tweet_count': 8590}
{u'user_id': u'@BystronicSales', u'user_name': u'Bystronic Sales AG', u'hashtags': [u'bystronic'], u'followers': 306, u'following': 73, u'_id': ObjectId('5ada4428ec661529fc12dace'), u'tweet_count': 1184}
{u'user_id': u'@Leaguend', u'user_name': u'Peter', u'hashtags': [], u'followers': 99, u'following': 752, u'_id': ObjectId('5ada4428ec661529fc12dacf'), u'tweet_count': 2912}
{u'user_id': u'@tmj_CAP_it', u'user_name': u'TMJ - CAP IT Jobs', u'hashtags': [u'hiring'], u'followers': 398, u'following': 302, u'_id': ObjectId('5ada4428ec661529fc12dad0'), u'tweet_count': 92}
{u'user_id': u'@rodulfox', u'user_name': u'Juan R. Rodulfo M

In [17]:
output= tweet.find({})
for data in list(output):
    print data

{u'user_id': u'@ExpoDX', u'tweet_contents': u'RT @ExpoDX: AI, Monitoring and Digital Transformation with @SaboTaylorDiab  @Loom_Systems #CloudNative #APM #Linux #Serverless #DevOps #Dat\u2026', u'hashtags': [u'cloudnative', u'apm', u'linux', u'serverless', u'devops'], u'tweet_id': u'968036614202150912', u'retweets': 2, u'urls': u'NO_URL', u'time': u'08:14:48', u'date': u'2018-02-26', u'favourites': 0, u'_id': ObjectId('5ada44f2ec661529fc12dc5e')}
{u'user_id': u'@ExpoDX', u'tweet_contents': u'AI, Monitoring and Digital Transformation with @SaboTaylorDiab  @Loom_Systems #CloudNative #APM #Linux #Serverless\u2026 https://t.co/5CaXydsQEp', u'hashtags': [u'cloudnative', u'apm', u'linux', u'serverless'], u'tweet_id': u'968036597634564096', u'retweets': 2, u'urls': u'https://twitter.com/i/web/status/968036597634564096', u'time': u'08:14:44', u'date': u'2018-02-26', u'favourites': 1, u'_id': ObjectId('5ada44f2ec661529fc12dc5f')}
{u'user_id': u'@TechNewsRprt', u'tweet_contents': u'RT @TamaraMcC

{u'user_id': u'@_tatianaacosta', u'tweet_contents': u'Having a michelada so I can sleep when I get home.. because I\u2019m the morning I have @salesforce automation processes\u2026 https://t.co/MaClL3eSwa', u'hashtags': [], u'tweet_id': u'968738254471168000', u'retweets': 0, u'urls': u'https://twitter.com/i/web/status/968738254471168000', u'time': u'06:42:52', u'date': u'2018-02-28', u'favourites': 0, u'_id': ObjectId('5ada44f4ec661529fc12e3d7')}
{u'user_id': u'@itestingwhiz', u'tweet_contents': u'A couple of ways of analyzing #Returns on #TestAutomation: https://t.co/uiZootQy7x #ROI https://t.co/NnIQvyB8FQ', u'hashtags': [u'returns', u'testautomation', u'roi'], u'tweet_id': u'968738069246554112', u'retweets': 0, u'urls': u'https://goo.gl/hLmBLe', u'time': u'06:42:08', u'date': u'2018-02-28', u'favourites': 0, u'_id': ObjectId('5ada44f4ec661529fc12e3d8')}
{u'user_id': u'@LaraFawzy', u'tweet_contents': u'The 2018 #CiscoACR: Defenders report greater reliance on automation for their #cybe

{u'user_id': u'@akdm_bot', u'tweet_contents': u'RT @DrDataScientist: ICYDK: Using Neural Networks for sales prospecting: No one wants to be sold but everyone wants to buy. Most of us ha\u2026', u'hashtags': [], u'tweet_id': u'975833399997775872', u'retweets': 294, u'urls': u'NO_URL', u'time': u'20:36:27', u'date': u'2018-03-19', u'favourites': 0, u'_id': ObjectId('5ada44f6ec661529fc12e9dc')}
{u'user_id': u'@ninjahade', u'tweet_contents': u'#Share #MustRead #StudyDisciplinesRinseRepeat #DataScience https://t.co/xP6fbrX5Qq', u'hashtags': [u'share', u'mustread', u'studydisciplinesrinserepeat', u'datascience'], u'tweet_id': u'975833158217338880', u'retweets': 0, u'urls': u'https://twitter.com/lisachwinter/status/975830814616379392', u'time': u'20:35:29', u'date': u'2018-03-19', u'favourites': 0, u'_id': ObjectId('5ada44f6ec661529fc12e9dd')}
{u'user_id': u'@ecolandlab', u'tweet_contents': u'RT @lolafarinas: Looking forward to use @Vizzuality. Great platform for satellite images visualizatio